# Exploratory Data Analysis of Climate Models and Precipitation Forecasts

In [2]:
# Import necessary packages
# !pip install hvplot
# !pip install jupyter_bokeh
# !pip install geoviews
import xarray as xr
import hvplot.xarray  # Provides .hvplot methods for xarray objects
import panel as pn
import geoviews as gv   # For geographic overlays (e.g. coastlines)
from cartopy import crs
import holoviews as hv
import glob
import os
import numpy as np
import matplotlib.pyplot as plt
import cartopy.crs as ccrs
import cartopy.feature as cfeature

# Activate the Bokeh backend for interactive plotting
hv.extension('bokeh')
gv.extension('bokeh')
pn.extension()


In [4]:
# Start with the GFDL model
GFDL = xr.open_mfdataset('data/NMME/GFDL-SPEAR/*.nc')

# Rename
GFDL = GFDL.rename({'Y': 'latitude',
                    'X': 'longitude',
                    'prec': 'precip',
                    'S': 'time',
                    'L': 'lead_time',
                    'M': 'ensemble_member'})

In [5]:
# Ensure the "time" coordinate is in datetime format (if not already)
GFDL["time"] = xr.decode_cf(GFDL)["time"]

# Extract unique values for the widgets
months = sorted(set(GFDL["time"].dt.month.values))
years = sorted(set(GFDL["time"].dt.year.values))
lead_times = sorted(set(GFDL["lead_time"].values))
ensemble_members = sorted(set(GFDL["ensemble_member"].values))  # Change if your ensemble dimension name is different

# Create Panel widgets
month_slider = pn.widgets.IntSlider(name="Month", start=min(months), end=max(months), step=1, value=5)
year_slider = pn.widgets.IntSlider(name="Year", start=min(years), end=max(years), step=1, value=years[2])
lead_slider = pn.widgets.FloatSlider(name="Lead Time", start=0.5, end=11.5, step=1, value=0.5)
ensemble_selector = pn.widgets.Select(name="Ensemble Member", options=ensemble_members, value=ensemble_members[0])


In [6]:
# Define interactive function for predictive model
def plot_precip_heatmap(month, year, lead_time, model):
    filtered_ds = model.sel(lead_time=lead_time).where(
    (model["time"].dt.month == month) & (model["time"].dt.year == year),
    drop=True)

    # the parameters in Orthographic() function control the rotation
    # for some reason, projections like Robinson dont work, it bugs out
    return filtered_ds["precip"].hvplot.quadmesh(
    x="longitude", y="latitude", colorbar=True,
    projection=crs.Orthographic(central_latitude=0, central_longitude=0), project=True,
    global_extent=True, cmap='RdYlGn', coastline=True,
    title=f"Precipitation - {month}/{year}, Lead: {lead_time}"
)

In [7]:
# Bind widgets with function
interactive_plot = pn.bind(plot_precip_heatmap, month=month_slider, year=year_slider, lead_time=lead_slider, model=GFDL)

# Display
pn.Column(month_slider, year_slider, lead_slider, interactive_plot).servable()

Column
    [0] IntSlider(end=np.int64(12), name='Month', start=np.int64(1), value=5)
    [1] IntSlider(end=np.int64(2025), name='Year', start=np.int64(1991), value=np.int64(1993))
    [2] FloatSlider(end=11.5, name='Lead Time', start=0.5, step=1, value=0.5)
    [3] ParamFunction(function, _pane=Row, defer_load=False)

# View CHIRPS Interactively

In [ ]:
# Running an interactive map for chirps is super slow and memory intensive, look into subsetting

# # Load in chirps
# chirps_path = '/content/drive/My Drive/capstone_data/CHIRPS/*.nc'

# chirps = xr.open_mfdataset(chirps_path, parallel=True)

In [ ]:
# # Ensure the "time" coordinate is in datetime format (if not already)
# chirps["time"] = xr.decode_cf(chirps)["time"]

# # Extract unique values for the widgets
# months = sorted(set(chirps["time"].dt.month.values))
# years = sorted(set(chirps["time"].dt.year.values))

# # Create interactive widgets
# year_slider = pn.widgets.IntSlider(name="Year", start=1981, end=2025, step=1, value=2020)
# month_slider = pn.widgets.IntSlider(name="Month", start=1, end=12, step=1, value=6)

In [ ]:
# # Define interactive function for chirps
# def plot_precip_heatmap_chirps(month, year):
#     filtered_ds = chirps.sel(time=(chirps["time"].dt.month == month) & (chirps["time"].dt.year == year),
#                              drop=True) # Change is here

#     # the parameters in Orthographic() function control the rotation
#     # for some reason, projections like Robinson dont work, it bugs out
#     return filtered_ds["precip"].hvplot.quadmesh(
#     x="longitude", y="latitude", colorbar=True,
#     projection=crs.Orthographic(central_latitude=0, central_longitude=0), project=True,
#     global_extent=True, cmap='jet', coastline=True,
#     title=f"Chirps Precipitation - Month: {month}, Year: {year}" # lead_time removed, was not defined
# )

In [ ]:
# # Link sliders to function
# interactive_map = pn.bind(plot_precip_heatmap_chirps, month=month_slider, year=year_slider)

# # Display
# pn.Column(month_slider, year_slider, interactive_map).servable()